#### ОТП БАНК Фомин Фёдор

Речь пойдет о решении конкурсной задачи предсказания отклика ОТП Банка (обсуждение задачи можно найти на сайте http://www.machinelearning.ru, а обсуждение итогов конкурса – в презентации http://www.forecsys.ru/get_file.php?id=558). Необходимые нам данные записаны в файле Credit_OTP.csv. Исходная выборка содержит записи о 15223 клиентах, классифицированных на два класса:  0 – отклика не было (13 411 клиентов) и 1 – отклик был (1812 клиентов). По каждому наблюдению (клиенту) фиксируются 52 исходные переменные.

Блок 1
Импорт библиотек и считывание датафрейма

In [92]:
# Импортируем библиотеки
import pandas as pd
import numpy as np
import pandas_profiling
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
import warnings
warnings.filterwarnings('ignore')

# Импортируем классы
from sklearn.impute import SimpleImputer
from sklearn.model_selection import StratifiedKFold
from sklearn.model_selection import GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import PowerTransformer
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.base import BaseEstimator, TransformerMixin
from category_encoders import TargetEncoder

# Импортируем функции
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import train_test_split

In [93]:
# Грузим класс для импутации пропусков по группировке 
class ImputeGroupBy(BaseEstimator, TransformerMixin):
    """
    Параметры:
    method_impute_cat: метод импутации категориальных признаков. mode
    method_impute_num: метод импутации количественных признаков. mean|median|mode
    group_by_col: по какой группе делаем группировку
    """
    def __init__(self, group_by_col, method_impute_cat="mode", method_impute_num="mean", copy=True):
        self.method_impute_cat = method_impute_cat
        self.method_impute_num = method_impute_num
        self.group_by_col = group_by_col
        self.copy = copy
    
    def fit(self, X, y=None):
        # Создаём копию, чтобы не менять исходный датафрейм
        if self.copy:
            X = X.copy()

        # Словарь преобразований
        self._encoder_dict = {}

        # Проверяем тип данных входного массива. 
        # Если не DataFrame, то преобразуем в него   
        if isinstance(X, pd.DataFrame) == False:
            X = pd.DataFrame(X)
            X = X.astype(object).replace("None", np.nan)
            X = X.astype(object).replace("nan", np.nan)
        
        for col in X.loc[:, X.columns != self.group_by_col].columns:
            if X[col].dtype == "object":
                self.dict_col = X.groupby(self.group_by_col)[col].\
                    agg(lambda x: next(iter(x.mode()), None)).to_frame().to_dict()
                self._encoder_dict.update(self.dict_col)
            else:
                if self.method_impute_num == "mean":
                    self.dict_col = X.groupby(self.group_by_col)[col].\
                        agg(lambda x: x.mean()).to_frame().to_dict()
                    self._encoder_dict.update(self.dict_col)
                elif self.method_impute_num == "median":
                    self.dict_col = X.groupby(self.group_by_col)[col].\
                        agg(lambda x: x.median()).to_frame().to_dict()
                    self._encoder_dict.update(self.dict_col)
                elif self.method_impute_num == "mode":
                    self.dict_col = X.groupby(self.group_by_col)[col].\
                        agg(lambda x: next(iter(x.mode()), None)).to_frame().to_dict()
                    self._encoder_dict.update(self.dict_col)

        return self

    def transform(self, X):
        # Создаём копию, чтобы не менять исходный датафрейм
        if self.copy:
            X = X.copy()

        # Проверяем тип данных входного массива.
        # Если не DataFrame, то преобразуем в него
        if isinstance(X, pd.DataFrame) == False:
            X = pd.DataFrame(X)
            X = X.astype(object).replace("None", np.nan)
            X = X.astype(object).replace("nan", np.nan)

        for col in X.loc[:, X.columns != self.group_by_col].columns:
            X[col] = X[col].fillna(X[self.group_by_col].map(self._encoder_dict[col]))

        return X

In [94]:
# Считываем файл
df_default = pd.read_csv(
                        'Credit_OTP.csv',
                        sep=';',
                        encoding='windows-1251'
                        )

In [95]:
# Делаем копию, чтобы не менялись данные в исходном датафрейме df_default
df = df_default.copy()

In [96]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15223 entries, 0 to 15222
Data columns (total 52 columns):
AGREEMENT_RK                  15223 non-null int64
TARGET                        15223 non-null int64
AGE                           15223 non-null int64
SOCSTATUS_WORK_FL             15223 non-null int64
SOCSTATUS_PENS_FL             15223 non-null int64
GENDER                        15223 non-null int64
CHILD_TOTAL                   15223 non-null int64
DEPENDANTS                    15223 non-null int64
EDUCATION                     15223 non-null object
MARITAL_STATUS                15223 non-null object
GEN_INDUSTRY                  13856 non-null object
GEN_TITLE                     13856 non-null object
ORG_TP_STATE                  13856 non-null object
ORG_TP_FCAPITAL               13858 non-null object
JOB_DIR                       13856 non-null object
FAMILY_INCOME                 15223 non-null object
PERSONAL_INCOME               15223 non-null object
REG_ADDRESS_PRO

In [97]:
# Переводим из object во float
l_obj_to_float = [
                    'PERSONAL_INCOME', 
                    'CREDIT', 
                    'FST_PAYMENT',
                    'LOAN_AVG_DLQ_AMT', 
                    'LOAN_MAX_DLQ_AMT'
                 ]

for i in l_obj_to_float:
    df[i] = df[i].str.replace(',', '.').astype('float')

In [98]:
# Смотрим количество пустых значений у предикторов
df.isna().sum().to_frame('N_ZEROS')

N_ZEROS
AGREEMENT_RK                      0
TARGET                            0
AGE                               0
SOCSTATUS_WORK_FL                 0
SOCSTATUS_PENS_FL                 0
GENDER                            0
CHILD_TOTAL                       0
DEPENDANTS                        0
EDUCATION                         0
MARITAL_STATUS                    0
GEN_INDUSTRY                   1367
GEN_TITLE                      1367
ORG_TP_STATE                   1367
ORG_TP_FCAPITAL                1365
JOB_DIR                        1367
FAMILY_INCOME                     0
PERSONAL_INCOME                   0
REG_ADDRESS_PROVINCE              0
FACT_ADDRESS_PROVINCE             0
POSTAL_ADDRESS_PROVINCE           0
TP_PROVINCE                     295
REGION_NM                         1
REG_FACT_FL                       0
FACT_POST_FL                      0
REG_POST_FL                       0
REG_FACT_POST_FL                  0
REG_FACT_POST_TP_FL               0
FL_PRESENCE_FL                    0
OWN_AUTO                          0
AUTO_RUS_FL                       0
HS_PRESENCE_FL                    0
COT_PRESENCE_FL                   0
GAR_PRESENCE_FL                   0
LAND_PRESENCE_FL                  0
CREDIT                            0
TERM                              0
FST_PAYMENT                       0
DL_DOCUMENT_FL                    0
GPF_DOCUMENT_FL                   0
FACT_LIVING_TERM                  0
WORK_TIME                      1368
FACT_PHONE_FL                     0
REG_PHONE_FL                      0
GEN_PHONE_FL                      0
LOAN_NUM_TOTAL                    0
LOAN_NUM_CLOSED                   0
LOAN_NUM_PAYM                     0
LOAN_DLQ_NUM                      0
LOAN_MAX_DLQ                      0
LOAN_AVG_DLQ_AMT                  0
LOAN_MAX_DLQ_AMT                  0
PREVIOUS_CARD_NUM_UTILIZED    14935

In [99]:
# В данных у одного объекта присутсвует пустое значение предиктора REGION_NM
# Смотрим, какое значение у REG_ADDRESS_PROVINCE в этом объекте
df.loc[df['REGION_NM'].isnull(), 'REG_ADDRESS_PROVINCE'].values

# Применяем класс для импутации группировкой по признаку REG_ADDRESS_PROVINCE
r_nm_imp = ImputeGroupBy(group_by_col='REG_ADDRESS_PROVINCE')
r_nm_imp.fit(df)
df['REGION_NM'] = r_nm_imp.transform(df[['REGION_NM','REG_ADDRESS_PROVINCE']])

In [100]:
# Смотрим количество пустых значений у предикторов
df.isna().sum().to_frame('N_ZEROS')

N_ZEROS
AGREEMENT_RK                      0
TARGET                            0
AGE                               0
SOCSTATUS_WORK_FL                 0
SOCSTATUS_PENS_FL                 0
GENDER                            0
CHILD_TOTAL                       0
DEPENDANTS                        0
EDUCATION                         0
MARITAL_STATUS                    0
GEN_INDUSTRY                   1367
GEN_TITLE                      1367
ORG_TP_STATE                   1367
ORG_TP_FCAPITAL                1365
JOB_DIR                        1367
FAMILY_INCOME                     0
PERSONAL_INCOME                   0
REG_ADDRESS_PROVINCE              0
FACT_ADDRESS_PROVINCE             0
POSTAL_ADDRESS_PROVINCE           0
TP_PROVINCE                     295
REGION_NM                         0
REG_FACT_FL                       0
FACT_POST_FL                      0
REG_POST_FL                       0
REG_FACT_POST_FL                  0
REG_FACT_POST_TP_FL               0
FL_PRESENCE_FL                    0
OWN_AUTO                          0
AUTO_RUS_FL                       0
HS_PRESENCE_FL                    0
COT_PRESENCE_FL                   0
GAR_PRESENCE_FL                   0
LAND_PRESENCE_FL                  0
CREDIT                            0
TERM                              0
FST_PAYMENT                       0
DL_DOCUMENT_FL                    0
GPF_DOCUMENT_FL                   0
FACT_LIVING_TERM                  0
WORK_TIME                      1368
FACT_PHONE_FL                     0
REG_PHONE_FL                      0
GEN_PHONE_FL                      0
LOAN_NUM_TOTAL                    0
LOAN_NUM_CLOSED                   0
LOAN_NUM_PAYM                     0
LOAN_DLQ_NUM                      0
LOAN_MAX_DLQ                      0
LOAN_AVG_DLQ_AMT                  0
LOAN_MAX_DLQ_AMT                  0
PREVIOUS_CARD_NUM_UTILIZED    14935

In [101]:
# Если SOCSTATUS_PENS_FL=1 и WORK_TIME пустой,
# то вводим новый признак 'ПЕНСИЯ' в признаки
# ['GEN_INDUSTRY', 'GEN_TITLE','ORG_TP_STATE', 'ORG_TP_FCAPITAL', 'JOB_DIR']
# Считаем пенсионерами людей и младше 50, так как есть
# военная, полицейская, пенсия по потери кормильца, инвалидности и другие.

df['GEN_INDUSTRY'] = np.where((df['WORK_TIME'].isnull())
                            & (df['SOCSTATUS_PENS_FL'] == 1),
                              'ПЕНСИЯ', 
                               df['GEN_INDUSTRY'])

df['GEN_TITLE'] = np.where((df['WORK_TIME'].isnull())
                         & (df['SOCSTATUS_PENS_FL'] == 1),
                           'ПЕНСИЯ', 
                            df['GEN_TITLE'])

df['ORG_TP_STATE'] = np.where((df['WORK_TIME'].isnull())
                            & (df['SOCSTATUS_PENS_FL'] == 1),
                              'ПЕНСИЯ', 
                               df['ORG_TP_STATE'])

df['ORG_TP_FCAPITAL'] = np.where((df['WORK_TIME'].isnull())
                               & (df['SOCSTATUS_PENS_FL'] == 1),
                                 'ПЕНСИЯ', 
                                  df['ORG_TP_FCAPITAL'])

df['JOB_DIR'] = np.where((df['WORK_TIME'].isnull())
                       & (df['SOCSTATUS_PENS_FL'] == 1),
                         'ПЕНСИЯ', 
                          df['JOB_DIR'])

In [102]:
# Смотрим количество пустых значений у предикторов
df.isna().sum().to_frame('N_ZEROS')

N_ZEROS
AGREEMENT_RK                      0
TARGET                            0
AGE                               0
SOCSTATUS_WORK_FL                 0
SOCSTATUS_PENS_FL                 0
GENDER                            0
CHILD_TOTAL                       0
DEPENDANTS                        0
EDUCATION                         0
MARITAL_STATUS                    0
GEN_INDUSTRY                      1
GEN_TITLE                         1
ORG_TP_STATE                      1
ORG_TP_FCAPITAL                   1
JOB_DIR                           1
FAMILY_INCOME                     0
PERSONAL_INCOME                   0
REG_ADDRESS_PROVINCE              0
FACT_ADDRESS_PROVINCE             0
POSTAL_ADDRESS_PROVINCE           0
TP_PROVINCE                     295
REGION_NM                         0
REG_FACT_FL                       0
FACT_POST_FL                      0
REG_POST_FL                       0
REG_FACT_POST_FL                  0
REG_FACT_POST_TP_FL               0
FL_PRESENCE_FL                    0
OWN_AUTO                          0
AUTO_RUS_FL                       0
HS_PRESENCE_FL                    0
COT_PRESENCE_FL                   0
GAR_PRESENCE_FL                   0
LAND_PRESENCE_FL                  0
CREDIT                            0
TERM                              0
FST_PAYMENT                       0
DL_DOCUMENT_FL                    0
GPF_DOCUMENT_FL                   0
FACT_LIVING_TERM                  0
WORK_TIME                      1368
FACT_PHONE_FL                     0
REG_PHONE_FL                      0
GEN_PHONE_FL                      0
LOAN_NUM_TOTAL                    0
LOAN_NUM_CLOSED                   0
LOAN_NUM_PAYM                     0
LOAN_DLQ_NUM                      0
LOAN_MAX_DLQ                      0
LOAN_AVG_DLQ_AMT                  0
LOAN_MAX_DLQ_AMT                  0
PREVIOUS_CARD_NUM_UTILIZED    14935

In [103]:
# Вставляем 0 в PREVIOUS_CARD_NUM_UTILIZED и WORK_TIME. 
# Делить на тест и трейн не нужно, так как импутирование без привязки к значениям.

simp_pcnu_wt = SimpleImputer(strategy='constant', fill_value=0)
df[['PREVIOUS_CARD_NUM_UTILIZED', 'WORK_TIME']] = simp_pcnu_wt.fit_transform(df[['PREVIOUS_CARD_NUM_UTILIZED', 'WORK_TIME']])

In [104]:
# Вводим категорию, где не задана TP_PROVINCE
df['TP_PROVINCE'] = df['TP_PROVINCE'].fillna('ПУСТО')

In [105]:
# Убираем оставшуюся строку, где не задана GEN_INDUSTRY
df = df.loc[~(df['GEN_INDUSTRY'].isnull())] 

In [106]:
# Удадяем признак DL_DOCUMENT_FL, так как он содержит только одно уникальное значение 
df.drop('DL_DOCUMENT_FL', axis=1, inplace=True)

# Удадяем признак AGREEMENT_RK, так как он содержит id
df.drop('AGREEMENT_RK', axis=1, inplace=True)

In [107]:
# Заменяем значения предиктора FACT_LIVING_TERM, 
# когда срок жития на фактическом месте больше текущей продолжительности жизни
df['FACT_LIVING_TERM'] = np.where(((df['AGE'] * 12) < df['FACT_LIVING_TERM']),
                                    df['AGE'] * 12, 
                                    df['FACT_LIVING_TERM'])

# Заменяем значения предиктора WORK_TIME, 
# когда рабочий стаж больше текущей продолжительности жизни и 
df['WORK_TIME'] = np.where(((df['AGE'] * 12 - 192) < df['WORK_TIME']),
                             df['AGE'] * 12, 
                             df['WORK_TIME'])


In [108]:
# Убираем строку, где FACT_LIVING_TERM < 0: одна строка
df = df.loc[~(df['FACT_LIVING_TERM'] < 0)] 

# Убираем строку, где PERSONAL_INCOME < 100: одна строка
df = df.loc[~(df['PERSONAL_INCOME'] < 100)] 

In [109]:
# Добавляем бинарный признак, есть ли дети
df['CHILD_BIN'] = np.where((df['CHILD_TOTAL'] > 0),
                            1, 
                            0)

# Добавляем бинарный признак, есть ли иждивенцы
df['DEPENDANTS_BIN'] = np.where((df['DEPENDANTS'] > 0),
                                1, 
                                0)

In [110]:
# Считаем доход на одного ребенка. Если детей нет, то приравниваем ежемесячному доходу
df['INCOME_ON_CHILD'] = np.where((df['CHILD_TOTAL'] > 0),
                                 (df['PERSONAL_INCOME'] / df['CHILD_TOTAL']), 
                                  df['PERSONAL_INCOME'])

# Считаем доход на одного иждивенца. Если иждивенцев нет, то приравниваем ежемесячному доходу
df['INCOME_ON_DEPENDANTS'] = np.where((df['DEPENDANTS'] > 0),
                                      (df['PERSONAL_INCOME'] / df['DEPENDANTS']), 
                                       df['PERSONAL_INCOME'])

In [111]:
# Группируем признак ORG_TP_STATE для значений 'Частная компания' и 'Частная ком. с инос. капиталом'
df['ORG_TP_STATE'] = np.where((df['ORG_TP_STATE'] == 'Частная ком. с инос. капиталом'),
                               'Частная компания', 
                               df['ORG_TP_STATE'])

# Группируем признак EDUCATION для значений 'высшее', 'два и более', 'ученая степень'
df['EDUCATION'] = np.where( (df['EDUCATION'] == 'Ученая степень')
                          | (df['EDUCATION'] == 'Два и более высших образования'),
                            'Высшее', 
                            df['EDUCATION'])

# Признак PREVIOUS_CARD_NUM_UTILIZED превращаем в бинарный,
# присвоив '1' для всех значений >=1
df['PREVIOUS_CARD_NUM_UTILIZED'] = np.where((df['PREVIOUS_CARD_NUM_UTILIZED'] >= 1),
                                             1, 
                                             df['PREVIOUS_CARD_NUM_UTILIZED'])

# Признак OWN_AUTO превращаем в бинарный,
# присвоив '1' для всех значений >=1
df['OWN_AUTO'] = np.where((df['OWN_AUTO'] >= 1),
                           1, 
                           df['OWN_AUTO'])

In [112]:
# Разбиваем AGE на бины
bins = [0, 24, 34, 44, 60, np.inf]
names = ['<=24', '25-34', '35-44', '45-60', '60+']

df['AGERange'] = pd.cut(df['AGE'], bins, labels=names)
df['AGERange'] = df['AGERange'].astype('object')

In [113]:
# Логарифмируем признаки для приведения к нормальности
for col in [ 
            'PERSONAL_INCOME',
            'CREDIT',
            'FST_PAYMENT',
            'FACT_LIVING_TERM',
            'WORK_TIME',
            'LOAN_NUM_PAYM',
            'LOAN_DLQ_NUM',
            'LOAN_MAX_DLQ',
            'LOAN_AVG_DLQ_AMT',
            'LOAN_MAX_DLQ_AMT',
            'INCOME_ON_CHILD',
            'INCOME_ON_DEPENDANTS'
           ]:
    df[col] = np.log(df[col]+1)


In [114]:
df.drop(['CHILD_TOTAL', 'DEPENDANTS', 'AGE', 'GEN_PHONE_FL', 'REG_FACT_POST_FL', 'ORG_TP_FCAPITAL'], axis=1, inplace=True)

In [115]:
pandas_profiling.ProfileReport(df)

In [124]:
# Разбиваем выборку на тестовую и обучающую

X_train, X_test, y_train, y_test = train_test_split(df.drop('TARGET', axis=1),
                                                    df['TARGET'],
                                                    test_size=0.3,
                                                    shuffle=True,
                                                    stratify=df['TARGET'],
                                                    random_state=28)

In [117]:
# Обучение Логистическая регрессия с дамми кодированием

cat_columns_logreg = X_train.dtypes[X_train.dtypes == 'object'].index

num_columns_logreg = []
for col in X_train.dtypes[X_train.dtypes != 'object'].index:
    if X_train[col].nunique() > 2:
        num_columns_logreg.append(col)
        
# num_columns_logreg = ['AGE', 'PERSONAL_INCOME', 'CREDIT', 'FST_PAYMENT', 'TERM',\
#                    'FACT_LIVING_TERM', 'WORK_TIME', 'INCOME_ON_CHILD', 'INCOME_ON_DEPENDANTS',\
#                    'LOAN_AVG_DLQ_AMT', 'LOAN_DLQ_NUM', 'LOAN_NUM_CLOSED', 'LOAN_NUM_PAYM', 'LOAN_NUM_TOTAL']

num_pipe_logreg = Pipeline([
                           ('scaler', StandardScaler())
                            ])

cat_pipe_logreg = Pipeline([
                            ('ohe', OneHotEncoder(sparse=False, handle_unknown='ignore'))
                            ])

transformers = [
                ('num', num_pipe_logreg, num_columns_logreg),
                ('cat', cat_pipe_logreg, cat_columns_logreg)
                ]

transformer = ColumnTransformer(transformers=transformers)

ml_pipe = Pipeline([
                    ('tf', transformer),
                    ('logreg', LogisticRegression())
                    ])

param_grid = {
              'logreg__C':[.01, .1, .5, 1, 5, 10, 100]  
             }

cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=28)

gs = GridSearchCV(
                  ml_pipe,
                  param_grid,
                  scoring='roc_auc',
                  cv=cv
                )

gs.fit(X_train, y_train)
print("Наилучшие значения гиперпараметров: {}".format(gs.best_params_))
print("Наилучшее значение AUC на обучающих выборках: {:.4f}".format(gs.best_score_))
print("AUC на тестовой выборке: {:.4f}".format(roc_auc_score(y_test, gs.predict_proba(X_test)[:, 1])))

Наилучшие значения гиперпараметров: {'logreg__C': 0.01}
Наилучшее значение AUC на обучающих выборках: 0.6735
AUC на тестовой выборке: 0.6859


In [134]:
# Обучение Логистическая регрессия c target encoder

cat_columns_logreg = X_train.dtypes[X_train.dtypes == 'object'].index

num_columns_logreg = []
for col in X_train.dtypes[X_train.dtypes != 'object'].index:
    if X_train[col].nunique() > 2:
        num_columns_logreg.append(col)
        
# num_columns_logreg = ['AGE', 'PERSONAL_INCOME', 'CREDIT', 'FST_PAYMENT', 'TERM',\
#                    'FACT_LIVING_TERM', 'WORK_TIME', 'INCOME_ON_CHILD', 'INCOME_ON_DEPENDANTS',\
#                    'LOAN_AVG_DLQ_AMT', 'LOAN_DLQ_NUM', 'LOAN_NUM_CLOSED', 'LOAN_NUM_PAYM', 'LOAN_NUM_TOTAL']

num_pipe_logreg = Pipeline([
                            ('scaler', StandardScaler())
                            ])

cat_pipe_logreg = Pipeline([
                            ('tarenc', TargetEncoder())
                            ])

transformers = [
                ('num', num_pipe_logreg, num_columns_logreg),
                ('cat', cat_pipe_logreg, cat_columns_logreg)
                ]

transformer = ColumnTransformer(transformers=transformers)

ml_pipe = Pipeline([
                    ('tf', transformer),
                    ('logreg', LogisticRegression())
                    ])

param_grid = {
              'logreg__C':[.01, .1, .5, 1, 5, 10, 20, 50], 
              'tf__cat__tarenc__min_samples_leaf':[1, 2, 4, 40, 400, 800]
             }

cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=28)

gs = GridSearchCV(
                  ml_pipe,
                  param_grid,
                  scoring='roc_auc',
                  cv=cv,
                  verbose=1
                )

gs.fit(X_train, y_train)
print("Наилучшие значения гиперпараметров: {}".format(gs.best_params_))
print("Наилучшее значение AUC на обучающих выборках: {:.4f}".format(gs.best_score_))
print("AUC на тестовой выборке: {:.4f}".format(roc_auc_score(y_test, gs.predict_proba(X_test)[:, 1])))

Fitting 5 folds for each of 48 candidates, totalling 240 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 240 out of 240 | elapsed:  2.3min finished


Наилучшие значения гиперпараметров: {'logreg__C': 20, 'tf__cat__tarenc__min_samples_leaf': 400}
Наилучшее значение AUC на обучающих выборках: 0.6737
AUC на тестовой выборке: 0.6852
